In [21]:
Pkg.add("GLM")

  Updating registry at `C:\Users\Matt\.julia\registries\General`


  likely near C:\Users\Matt\.julia\packages\IJulia\DL02A\src\kernel.jl:41


  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 %1.2 % % Resolving package versions...
 Installed Arpack ──────── v0.3.0
 Installed Rmath ───────── v0.5.0
 Installed QuadGK ──────── v2.0.2
 Installed Parsers ─────── v0.2.14
 Installed GLM ─────────── v1.0.1
 Installed PDMats ──────── v0.9.5
 Installed StatsFuns ───── v0.7.0
 Installed StatsModels ─── v0.3.1
 Installed Distributions ─ v0.16.4
  Updating `C:\Users\Matt\.julia\environments\v0.7\Project.toml`
  [38e38edf] + GLM v1.0.1
  Updating `C:\Users\Matt\.julia\environments\v0.7\Manifest.toml`
  [7d9fca2a] + Arpack v0.3.0
  [31c24e10] + Distributions v0.16.4
  [38e38edf] + GLM v1.0.1
  [90014a1f] + PDMats v0.9.5
  [69de0a69] ↑ Parsers v0.2.13 ⇒ v0.2.14
  [1fd47b50] + QuadGK v2.0.2
  [79098fc4] + Rmath v0.5.0
  [4c63d2b9] + StatsFuns v0.7.0
  [3eaba693] + StatsModels v0.3.1
  [4607b0f0] + SuiteSparse 
  Building Rmath ─→ `C:\Users\Matt\.julia\package

In [ ]:
Pkg.add("Flux")

In [22]:
using Plots
using Flux, Flux.Data.MNIST ## this is the Julia package for deep learning 
using Flux: onehotbatch, argmax, crossentropy, throttle, mse
using Base.Iterators: repeated, partition
using GLM

┌ Info: Precompiling GLM [38e38edf-8417-5370-95a0-9cbb8c7f171a]
└ @ Base loading.jl:1187


In [2]:
include("postgresql.jl")

loaded


stream_to_dataframe (generic function with 1 method)

In [44]:
connection_dir = "./pitch-tunneling"

user, pw = open("pw_pitch_tunneling.txt") do file
    readlines(file)
end

username = user
password = pw

conn = connect_pitch_tunneling(connection_dir, username, password)

Connecting to pitch-tunneling database.
Data are stored in 'pitchtunnelingtest' and 'pitchtunnelingtrain' tables.


PostgreSQL connection (CONNECTION_OK) with parameters:
  user = user1
  password = ********************
  dbname = pitch-tunneling
  host = 141.211.55.211
  port = 58421
  client_encoding = UTF8
  application_name = LibPQ.jl
  sslmode = verify-ca
  sslcompression = 1
  sslcert = ./pitch-tunneling/postgresql.crt
  sslkey = ./pitch-tunneling/postgresql.key
  sslrootcert = ./pitch-tunneling/root.crt
  krbsrvname = postgres
  target_session_attrs = any

In [19]:
query = """
  SELECT ordinal_position,
         column_name,
         data_type,
         numeric_precision
    FROM information_schema.columns
   WHERE table_name = 'pitchtunnelingtrain'
ORDER BY ordinal_position;
"""
result = execute(conn, query)

#display list of columns as a data frame
data = Data.stream!(result, Data.Table)
DataFrame(data)

48×4 DataFrame. Omitted printing of 2 columns
│ Row │ ordinal_position │ column_name                       │
│     │ Int32⍰           │ Union{Missing, String}            │
├─────┼──────────────────┼───────────────────────────────────┤
│ 1   │ 1                │ pitchguid                         │
│ 2   │ 2                │ gamepk                            │
│ 3   │ 3                │ batterid                          │
│ 4   │ 4                │ pitcherid                         │
│ 5   │ 5                │ pitchtype                         │
│ 6   │ 6                │ venueid                           │
│ 7   │ 7                │ islhp                             │
│ 8   │ 8                │ islhb                             │
│ 9   │ 9                │ inning                            │
│ 10  │ 10               │ istop                             │
⋮
│ 38  │ 38               │ tunnellocationy                   │
│ 39  │ 39               │ tunnellocationz                   │
│ 40  │ 40               │ trajectoryverticalapproachangle   │
│ 41  │ 41               │ trajectoryhorizontalapproachangle │
│ 42  │ 42               │ trajectoryverticalbreak           │
│ 43  │ 43               │ trajectorylocationx               │
│ 44  │ 44               │ trajectorylocationy               │
│ 45  │ 45               │ trajectorylocationz               │
│ 46  │ 46               │ atbatnumber                       │
│ 47  │ 47               │ pitchnumber                       │
│ 48  │ 48               │ runvalue                          │

In [5]:
#lets look at a suggested subset of the data: left handed pichers, left handed batters, and only fastballs/sinkers
#leave out missing runvalue data
query = """
    SELECT trajectoryverticalbreak, tunnellocationx, tunnellocationy, tunnellocationz, runvalue
    FROM pitchtunnelingtrain
    WHERE islhp = '1' AND islhb = '1' AND (pitchtype = 'FF' OR pitchtype = 'FT' OR pitchtype = 'SI') AND runvalue IS NOT NULL;
"""

data = stream_to_dataframe(conn, query)

39620×5 DataFrame. Omitted printing of 2 columns
│ Row   │ trajectoryverticalbreak │ tunnellocationx │ tunnellocationy │
│       │ Union{Missing, Float64} │ Float64⍰        │ Float64⍰        │
├───────┼─────────────────────────┼─────────────────┼─────────────────┤
│ 1     │ -3.07861                │ 1.66127         │ 23.8            │
│ 2     │ -2.85711                │ 0.562368        │ 23.8            │
│ 3     │ -1.73779                │ 0.636278        │ 23.8            │
│ 4     │ -2.19986                │ 0.684391        │ 23.8            │
│ 5     │ -2.49878                │ 2.16153         │ 23.8            │
│ 6     │ -2.70107                │ 1.16315         │ 23.8            │
│ 7     │ -2.77534                │ 1.41148         │ 23.8            │
│ 8     │ -2.96358                │ 0.794065        │ 23.8            │
│ 9     │ -2.76706                │ 1.25884         │ 23.8            │
│ 10    │ -1.97781                │ 1.68171         │ 23.8            │
⋮
│ 39610 │ -1.09328                │ 0.220081        │ 23.8            │
│ 39611 │ -1.92421                │ -0.135091       │ 23.8            │
│ 39612 │ -2.0688                 │ 0.815136        │ 23.8            │
│ 39613 │ -1.64761                │ -0.482121       │ 23.8            │
│ 39614 │ -1.65641                │ 0.150227        │ 23.8            │
│ 39615 │ -1.55934                │ 1.5471          │ 23.8            │
│ 39616 │ -1.61466                │ -0.00707948     │ 23.8            │
│ 39617 │ -1.7158                 │ 0.630527        │ 23.8            │
│ 39618 │ -1.15557                │ 0.319511        │ 23.8            │
│ 39619 │ -1.91341                │ 1.08101         │ 23.8            │
│ 39620 │ -2.90661                │ 1.19493         │ 23.8            │

In [6]:
X = convert(Array,data[:,1:4])';
Y = parse.(Float64,data[:,5])';

┌ Warning: indexing with colon as row will create a copy in the future use df[col_inds] to get the columns without copying
│   caller = top-level scope at In[6]:1
└ @ Core In[6]:1
┌ Warning: indexing with colon as row will create a copy in the future use df[col_inds] to get the columns without copying
│   caller = top-level scope at In[6]:2
└ @ Core In[6]:2


In [7]:
loss_fn = mse
n = 10
m = Chain(Dense(4, n),Dense(n,n,relu),Dense(n,1)) ## TODO: Replace ?? -- Hint: What should it be for the dataset? 
loss(x, y) = loss_fn(m(x), y) 
evalcb = () -> @show([loss(X,Y)])
dataset = Base.Iterators.repeated((X, Y), 500)
opt = ADAM(params(m)) 
Flux.train!(loss, dataset, opt, cb = throttle(evalcb, 0.01))

[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[1.37751 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.985333 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[1.16676 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.819787 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.863796 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.905648 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.7748 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.772854 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.789156 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.729124 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.719331 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.717685 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.68429 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.67515 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{

[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0463663 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0461845 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0460125 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0458494 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0456948 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.045548 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0454086 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0452759 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0451497 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0450294 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0449148 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0448053 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0447009 (tracked)]
[loss(X, Y)] = Flux.Tracker.TrackedReal{Float64}[0.0446011 (tracked)]
[loss(X, Y)] = Flux.T

In [9]:
m(X)[1]-Y[1]

-0.38999760549196555 (tracked)

In [45]:
query = """
    SELECT releasepositionx, releasepositionz, tunnellocationx, tunnellocationz, runvalue
    FROM pitchtunnelingtrain
    WHERE islhp = '1' AND islhb = '1' AND (pitchtype = 'FF' OR pitchtype = 'FT' OR pitchtype = 'SI') AND runvalue IS NOT NULL;
"""

data = stream_to_dataframe(conn, query)

39620×5 DataFrame. Omitted printing of 2 columns
│ Row   │ releasepositionx │ releasepositionz │ tunnellocationx │
│       │ Float64⍰         │ Float64⍰         │ Float64⍰        │
├───────┼──────────────────┼──────────────────┼─────────────────┤
│ 1     │ 0.956657         │ 6.15729          │ 0.478435        │
│ 2     │ 1.3332           │ 5.89732          │ 0.0669699       │
│ 3     │ 0.648763         │ 6.22676          │ -0.107854       │
│ 4     │ 1.22012          │ 5.96644          │ 0.486336        │
│ 5     │ 0.896023         │ 6.11476          │ -0.26913        │
│ 6     │ 1.13495          │ 6.00583          │ 0.833505        │
│ 7     │ 1.23857          │ 6.09027          │ 0.33979         │
│ 8     │ 0.924503         │ 6.02755          │ -0.0416601      │
│ 9     │ 0.760408         │ 6.1164           │ 0.492571        │
│ 10    │ 1.05099          │ 6.1672           │ 0.290195        │
⋮
│ 39610 │ 0.442481         │ 6.13531          │ 0.355186        │
│ 39611 │ 1.16003          │ 6.05483          │ 0.867519        │
│ 39612 │ 1.08154          │ 6.17385          │ 0.0335956       │
│ 39613 │ 1.87194          │ 5.8934           │ 1.61349         │
│ 39614 │ 0.965374         │ 6.07162          │ 0.922745        │
│ 39615 │ 1.69612          │ 6.17401          │ 1.08275         │
│ 39616 │ 1.58084          │ 5.75747          │ 0.269938        │
│ 39617 │ 0.760755         │ 5.86106          │ -0.822755       │
│ 39618 │ 1.28592          │ 5.87934          │ 0.273244        │
│ 39619 │ 1.32622          │ 5.85204          │ 0.529946        │
│ 39620 │ 0.858308         │ 6.13016          │ 0.441144        │

In [48]:
maximum(data[:,4])
#lm(@formula(tunnellocationx ~ releasepositionx), data)

┌ Warning: indexing with colon as row will create a copy in the future use df[col_inds] to get the columns without copying
│   caller = top-level scope at In[48]:1
└ @ Core In[48]:1


6.79278802646216

In [34]:
arr = convert(Array, data[:,1:4])
pinv(arr)

┌ Warning: indexing with colon as row will create a copy in the future use df[col_inds] to get the columns without copying
│   caller = top-level scope at In[34]:1
└ @ Core In[34]:1
Add `using LinearAlgebra` to your imports.
  likely near C:\Users\Matt\.julia\packages\IJulia\DL02A\src\kernel.jl:41


4×39620 Array{Float64,2}:
  5.15127e-5   0.000103464   4.10483e-5  …  -1.45692e-5   3.61993e-5
  9.12862e-6   1.50381e-5   -7.81495e-6      3.52356e-7   4.35521e-7
  2.90619e-5  -9.70709e-5   -3.70577e-5      4.46826e-5   8.26432e-6
 -2.51561e-5  -3.98387e-5    1.63002e-5      3.31076e-7  -3.36282e-6